In [1]:
from io import open
import os.path
from os import path
import random
import pickle
import pandas as pd
import scipy.signal
import torch
from torch.utils.data import Dataset, DataLoader
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import numpy as np

def load_data(csv_file):
    dataS = pd.read_csv(csv_file)
    F, L, LO, R, RO = 0, 0, 0, 0, 0
    for i in range(len(dataS['Label'].values)):
        if dataS['Label'].values[i] == 'Follow':
            F += 1
            dataS['Label'].values[i] = 0
        if dataS['Label'].values[i] == 'Left':
            L += 1
            dataS['Label'].values[i] = 1
        if dataS['Label'].values[i] == 'LeftOver':
            LO += 1
            dataS['Label'].values[i] = 2
        if dataS['Label'].values[i] == 'Right':
            R += 1
            dataS['Label'].values[i] = 3
        if dataS['Label'].values[i] == 'RightOver':
            RO += 1
            dataS['Label'].values[i] = 4
    # print(np.unique(dataS['Label']))
    print('Follow:', F, "Left:", L, "LeftOver:", LO, 'Right:', R, "RightOver:", RO)
    traj = np.zeros((np.shape(np.asarray(dataS))[0], 68 + 156))
    traj[:, :68] = np.asarray(dataS)
    for k in range(len(dataS)):
        time = dataS[['Global_Time']]
        time = np.asarray(time)[k]
        frame_time = dataS[dataS.Global_Time == time[0]]
        frame_time = np.asarray(frame_time)
        print(time[0], 'have', len(frame_time), 'vehicles')
        if frame_time.size > 1:
            dx = np.zeros(np.shape(frame_time)[0])
            dy = np.zeros(np.shape(frame_time)[0])
            vid = np.zeros(np.shape(frame_time)[0])

            for l in range(np.shape(frame_time)[0]):
                dx[l] = frame_time[l][4] - traj[k][4]
                dy[l] = frame_time[l][5] - traj[k][5]
                vid[l] = frame_time[l][0]
            dist = dx * dx + dy * dy  # 计算某一时刻下目标车辆与周围车辆之间的距离
            dist = np.sqrt(dist)

            lim = 39  # 限定最大的周围车辆数为39，

            if len(dist) > lim:
                idx = np.argsort(dist)  # 返回一个排序后的数组的索引,从小到大排列
                dx = np.array([dx[i] for i in idx[:lim]])
                dy = np.array([dy[i] for i in idx[:lim]])
                dist = np.array([dist[i] for i in idx[:lim]])
                vid = np.array([vid[i] for i in idx[:lim]])

            # left
            xl = dx[dx < -10]
            yl = dy[dx < -10]
            yl = yl[xl>-50]
            distl = dist[dx < -10]
            distl = distl[xl>-50]
            vidl = vid[dx < -10]
            vidl = vidl[xl>-50]
            xl = xl[xl>-50]
          #  print(xl,yl,vidl)
            # left top
            yl_top = yl[yl > 0]
            xl_top = xl[yl>0]
            xl_top = xl_top[yl_top<50]
            distl_top = distl[yl>0]
            distl_top = distl_top[yl_top<50]
            vidl_top = vidl[yl>0]
            vidl_top = vidl_top[yl_top<50]
            yl_top = yl_top[yl_top <50]
           # print(xl_top,yl_top,distl_top)
            # left bot
            yl_bot = yl[ yl < 0]
            xl_bot = xl[yl < 0]
            xl_bot = xl_bot[yl_bot>-50]
            distl_bot = distl[yl < 0]
            distl_bot = distl_bot[yl_bot>-50]
            vidl_bot = vidl[yl < 0]
            vidl_bot = vidl_bot[yl_bot>-50]
            yl_bot = yl_bot[yl_bot>-50]

            # center
            xc = dx[dx >= -10]
            yc = dy[dx >= -10]
            distc = dist[dx >= -10]
            vidc = vid[dx >= -10]

            yc = yc[xc < 10]
            #  print("s",yc)
            distc = distc[xc < 10]
            vidc = vidc[xc < 10]
            xc = xc[xc < 10]

            # center top
            yc_top = yc[yc > 0]
            xc_top = xc[yc > 0]
            xc_top = xc_top[yc_top < 50]
            distc_top = distc[yc > 0]
            distc_top = distc_top[yc_top < 50]
            vidc_top = vidc[yc > 0]
            vidc_top = vidc_top[yc_top < 50]
            yc_top = yc_top[yc_top < 50]
            # center bot
            yc_bot = yc[yc < 0]
            xc_bot = xc[yc < 0]
            xc_bot = xc_bot[yc_bot > -50]
            distc_bot = distc[yc < 0]
            distc_bot = distc_bot[yc_bot > -50]
            vidc_bot = vidc[yc < 0]
            vidc_bot = vidc_bot[yc_bot > -50]
            yc_bot = yc_bot[yc_bot > -50]

            # right
            xr = dx[dx < 50]
            yr = dy[dx < 50]
            yr = yr[xr > 10]
            distr = dist[dx < 50]
            distr = distr[xr > 10]
            vidr = vid[dx < 50]
            vidr = vidr[xr > 10]
            xr = xr[xr > 10]
          #  print(xr, yr, vidr)
            # reft top
            yr_top = yr[yr > 0]
            xr_top = xr[yr > 0]
            xr_top = xr_top[yr_top < 50]
            distr_top = distr[yr > 0]
            distr_top = distr_top[yr_top < 50]
            vidr_top = vidr[yr > 0]
            vidr_top = vidr_top[yr_top < 50]
            yr_top = yr_top[yr_top < 50]
          #  print(xr_top, yr_top, distr_top)
            # reft bot
            yr_bot = yr[yr < 0]
            xr_bot = xr[yr < 0]
            xr_bot = xr_bot[yr_bot > -50]
            distr_bot = distr[yr < 0]
            distr_bot = distr_bot[yr_bot > -50]
            vidr_bot = vidr[yr < 0]
            vidr_bot = vidr_bot[yr_bot > -50]
            yr_bot = yr_bot[yr_bot > -50]

            # parameters,挑选距离近的几个车辆
            mini_top = 7
            mini_bot = 6

            # left top
            iy = np.argsort(distl_top)
            iy = iy[0:min(mini_top, len(distl_top))]
            ltop = len(iy)
            xl_top = np.array([xl_top[i] for i in iy])
            yl_top = np.array([yl_top[i] for i in iy])
            distl_top = np.array([distl_top[i] for i in iy])
            vidl_top = np.array([vidl_top[i] for i in iy])

            # left bottom
            iy = np.argsort(distl_bot)
           # iy = np.array(list(reversed(iy)))  # 返回一个反转的迭代器,找出后面最近的车辆
            iy = iy[0:min(mini_bot, len(distl_bot))]
            lbot = len(iy)
            xl_bot = np.array([xl_bot[i] for i in iy])
            yl_bot = np.array([yl_bot[i] for i in iy])
            distl_bot = np.array([distl_bot[i] for i in iy])
            vidl_bot = np.array([vidl_bot[i] for i in iy])

            # center top
            iy = np.argsort(distc_top)
            iy = iy[0:min(mini_top, len(distc_top))]
            ctop = len(iy)
            xc_top = np.array([xc_top[i] for i in iy])
            yc_top = np.array([yc_top[i] for i in iy])
            distc_top = np.array([distc_top[i] for i in iy])
            vidc_top = np.array([vidc_top[i] for i in iy])

            # center bottom
            iy = np.argsort(distc_bot)
            #iy = np.array(list(reversed(iy)))
            iy = iy[0:min(mini_bot, len(distc_bot))]
            cbot = len(iy)
            xc_bot = np.array([xc_bot[i] for i in iy])
            yc_bot = np.array([yc_bot[i] for i in iy])
            distc_bot = np.array([distc_bot[i] for i in iy])
            vidc_bot = np.array([vidc_bot[i] for i in iy])

            # right top
            iy = np.argsort(distr_top)
            iy = iy[0:min(mini_top, len(distr_top))]
            rtop = len(iy)
            xr_top = np.array([xr_top[i] for i in iy])
            yr_top = np.array([yr_top[i] for i in iy])
            distr_top = np.array([distr_top[i] for i in iy])
            vidr_top = np.array([vidr_top[i] for i in iy])

            # right bottom
            iy = np.argsort(distr_bot)
           # iy = np.array(list(reversed(iy)))
            iy = iy[0:min(mini_bot, len(distr_bot))]
            rbot = len(iy)
            xr_bot = np.array([xr_bot[i] for i in iy])
            yr_bot = np.array([yr_bot[i] for i in iy])
            distr_bot = np.array([distr_bot[i] for i in iy])
            vidr_bot = np.array([vidr_bot[i] for i in iy])
            # 将目标车辆周围各个方向的Id合并如数组
            # traj[k, 68:68 + 6] = np.concatenate((np.zeros(6 - len(xl_bot)), xl_bot))
            # traj[k, 68+6:68 + 12] = np.concatenate((np.zeros(6 - len(yl_bot)), yl_bot))
            # traj[k, 68+12:68 + 18] = np.concatenate((np.zeros(6 - len(distl_bot)), distl_bot))
            # traj[k, 68+18:68+24] = np.concatenate((np.zeros(6 - len(vidl_bot)), vidl_bot))
            # left bot
            for i in range(lbot):
                traj[k, 68 + i * 4] = vidl_bot[i]
                traj[k, 68 + 1 + i * 4] = xl_bot[i]
                traj[k, 68 + 2 + i * 4] = yl_bot[i]
                traj[k, 68 + 3 + i * 4] = distl_bot[i]
            if lbot < mini_bot:
                for i in range(mini_bot - lbot):
                    traj[k, 68 + 3 + (lbot - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (lbot - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (lbot - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (lbot - 1) * 4 + 1 + 3 + i * 4] = 0
                # left top
            for i in range(ltop):
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + i * 4] = vidl_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 1 + i * 4] = xl_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 2 + i * 4] = yl_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + i * 4] = distl_top[i]
            if ltop < mini_top:
                for i in range(mini_top - ltop):
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ltop - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ltop - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ltop - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ltop - 1) * 4 + 1 + 3 + i * 4] = 0
            # center bot
            for i in range(cbot):
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + i * 4] = vidc_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 1 + i * 4] = xc_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 2 + i * 4] = yc_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + i * 4] = distc_bot[i]
            if cbot < mini_bot:
                for i in range(mini_bot - cbot):
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (cbot - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (   cbot - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (cbot - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( cbot - 1) * 4 + 1 + 3 + i * 4] = 0
            # center top
            for i in range(ctop):
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + i * 4] = vidc_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 1 + i * 4] = xc_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 2 + i * 4] = yc_top[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + i * 4] = distc_top[i]
            if ctop < mini_top:
                for i in range(mini_top - ctop):
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + (ctop - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + (ctop - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ctop - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (ctop - 1) * 4 + 1 + 3 + i * 4] = 0
            # right bot
            for i in range(rbot):
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + ( mini_top - 1) * 4 + 1 + i * 4] = vidr_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 1 + i * 4] = xr_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 2 + i * 4] = yr_bot[i]
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + i * 4] = distr_bot[i]
            if rbot < mini_bot:
                for i in range(mini_bot - rbot):
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (rbot - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (rbot - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (rbot - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( rbot - 1) * 4 + 1 + 3 + i * 4] = 0
            # right top
            for i in range(rtop):
                traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + i * 4] = vidr_top[i]
                traj[ k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + ( mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 1 + i * 4] = xr_top[i]
                traj[ k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 2 + i * 4] = yr_top[i]
                traj[ k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + i * 4] = distr_top[i]
            if rtop < mini_top:
                for i in range(mini_top - rtop):
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (rtop - 1) * 4 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + ( rtop - 1) * 4 + 1 + 1 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + ( mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (rtop - 1) * 4 + 1 + 2 + i * 4] = 0
                    traj[k, 68 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (mini_top - 1) * 4 + 1 + 3 + (mini_bot - 1) * 4 + 1 + 3 + (rtop - 1) * 4 + 1 + 3 + i * 4] = 0
    columns = ['Vehicle_ID', 'Frame_ID', 'Total_Frames', 'Global_Time', 'Local_X', 'Local_Y', 'Global_X', 'Global_Y',
               'v_Length', 'v_Width', 'v_Class', 'v_Vel', 'v_Acc', 'Lane_ID', 'Preceeding', 'Following', 'Space_Hdwy', 'Time_Hdwy',
               'Angle', 'L_rX', 'L_rY','L_rVel', 'L_rAcc', 'L_angle', 'L_Class', 'L_Len', 'L_Width', 'F_rX', 'F_rY', 'F_rVel', 'F_rAcc',
               'F_angle', 'F_Class', 'F_Len', 'F_Width','LL_rX', 'LL_rY', 'LL_rVel', 'LL_rAcc', 'LL_angle', 'LL_Class', 'LL_Len', 'LL_Width', 'LF_rX', 'LF_rY',
               'LF_rVel', 'LF_rAcc', 'LF_angle', 'LF_Class', 'LF_Len', 'LF_Width', 'RL_rX', 'RL_rY', 'RL_rVel', 'RL_rAcc', 'RL_angle', 'RL_Class',
               'RL_Len', 'RL_Width', 'RF_rX', 'RF_rY','RF_rVel', 'RF_rAcc', 'RF_angle', 'RF_Class', 'RF_Len', 'RF_Width', 'Label']
    print(len(columns))
    # left bot
    left_bot = []
    for i in range(1, mini_bot + 1):
        vidl_bot_ = 'Vidl_bot_{}'.format(i)
        left_bot.append(vidl_bot_)
        xl_bot_ = 'Xl_bot_{}'.format(i)
        left_bot.append(xl_bot_)
        yl_bot_ = 'Yl_bot_{}'.format(i)
        left_bot.append(yl_bot_)
        distl_bot_ = 'Distl_bot_{}'.format(i)
        left_bot.append(distl_bot_)
    # left top
    left_top = []
    for i in range(1, mini_top + 1):
        vidl_top_ = 'Vidl_top_{}'.format(i)
        left_top.append(vidl_top_)
        xl_top_ = 'Xl_top_{}'.format(i)
        left_top.append(xl_top_)
        yl_top_ = 'Yl_top_{}'.format(i)
        left_top.append(yl_top_)
        distl_top_ = 'Distl_top_{}'.format(i)
        left_top.append(distl_top_)
    # center bot
    center_bot = []
    for i in range(1, mini_bot + 1):
        vidc_bot_ = 'Vidc_bot_{}'.format(i)
        center_bot.append(vidc_bot_)
        xc_bot_ = 'Xc_bot_{}'.format(i)
        center_bot.append(xc_bot_)
        yc_bot_ = 'Yc_bot_{}'.format(i)
        center_bot.append(yc_bot_)
        distc_bot_ = 'Distc_bot_{}'.format(i)
        center_bot.append(distc_bot_)
    # center top
    center_top = []
    for i in range(1, mini_top + 1):
        vidc_top_ = 'Vidc_top_{}'.format(i)
        center_top.append(vidc_top_)
        xc_top_ = 'Xc_top_{}'.format(i)
        center_top.append(xc_top_)
        yc_top_ = 'Yc_top_{}'.format(i)
        center_top.append(yc_top_)
        distc_top_ = 'Distc_top_{}'.format(i)
        center_top.append(distc_top_)
    # right bot
    right_bot = []
    for i in range(1, mini_bot + 1):
        vidr_bot_ = 'Vidr_bot_{}'.format(i)
        right_bot.append(vidr_bot_)
        xr_bot_ = 'Xr_bot_{}'.format(i)
        right_bot.append(xr_bot_)
        yr_bot_ = 'Yr_bot_{}'.format(i)
        right_bot.append(yr_bot_)
        distr_bot_ = 'Distr_bot_{}'.format(i)
        right_bot.append(distr_bot_)
    # right top
    right_top = []
    for i in range(1, mini_top + 1):
        vidr_top_ = 'Vidr_top_{}'.format(i)
        right_top.append(vidr_top_)
        xr_top_ = 'Xr_top_{}'.format(i)
        right_top.append(xr_top_)
        yr_top_ = 'Yr_top_{}'.format(i)
        right_top.append(yr_top_)
        distr_top_ = 'Distr_top_{}'.format(i)
        right_top.append(distr_top_)

    columns = columns + left_bot + left_top + center_bot + center_top + right_bot + right_top
    print(len(columns))
    pd_data = pd.DataFrame(traj, columns=columns)
    print(left_bot,left_top,center_bot,center_top,right_bot,right_top)
    pd_data.to_csv('./data/WholeVdata2_interactive_formation_improve.csv')

In [2]:
load_data('./data/WholeVdata2.csv')

Follow: 191242 Left: 9471 LeftOver: 8449 Right: 3332 RightOver: 3163
1118848770700 have 5 vehicles
1118848770800 have 5 vehicles
1118848770900 have 5 vehicles
1118848771000 have 5 vehicles
1118848771100 have 5 vehicles
1118848771200 have 5 vehicles
1118848771300 have 5 vehicles
1118848771400 have 5 vehicles
1118848771500 have 5 vehicles
1118848771600 have 5 vehicles
1118848771700 have 5 vehicles
1118848771800 have 5 vehicles
1118848771900 have 5 vehicles
1118848772000 have 5 vehicles
1118848772100 have 5 vehicles
1118848772200 have 5 vehicles
1118848772300 have 5 vehicles
1118848772400 have 5 vehicles
1118848772500 have 5 vehicles
1118848772600 have 5 vehicles
1118848772700 have 5 vehicles
1118848772800 have 5 vehicles
1118848772900 have 5 vehicles
1118848773000 have 5 vehicles
1118848773100 have 5 vehicles
1118848773200 have 6 vehicles
1118848773300 have 6 vehicles
1118848773400 have 6 vehicles
1118848773500 have 6 vehicles
1118848773600 have 6 vehicles
1118848773700 have 6 vehicles
1

1118848803500 have 18 vehicles
1118848803600 have 18 vehicles
1118848803700 have 18 vehicles
1118848803800 have 18 vehicles
1118848803900 have 18 vehicles
1118848804000 have 18 vehicles
1118848804100 have 18 vehicles
1118848804200 have 18 vehicles
1118848804300 have 18 vehicles
1118848804400 have 18 vehicles
1118848804500 have 18 vehicles
1118848804600 have 18 vehicles
1118848804700 have 19 vehicles
1118848804800 have 19 vehicles
1118848804900 have 19 vehicles
1118848805000 have 20 vehicles
1118848805100 have 20 vehicles
1118848805200 have 20 vehicles
1118848805300 have 20 vehicles
1118848805400 have 20 vehicles
1118848805500 have 20 vehicles
1118848805600 have 20 vehicles
1118848805700 have 20 vehicles
1118848805800 have 20 vehicles
1118848805900 have 20 vehicles
1118848806000 have 20 vehicles
1118848806100 have 20 vehicles
1118848806200 have 21 vehicles
1118848806300 have 21 vehicles
1118848806400 have 21 vehicles
1118848806500 have 21 vehicles
1118848806600 have 21 vehicles
11188488

1118848788500 have 11 vehicles
1118848788600 have 11 vehicles
1118848788700 have 11 vehicles
1118848788800 have 11 vehicles
1118848788900 have 11 vehicles
1118848789000 have 11 vehicles
1118848789100 have 11 vehicles
1118848789200 have 11 vehicles
1118848789300 have 11 vehicles
1118848789400 have 11 vehicles
1118848789500 have 11 vehicles
1118848789600 have 11 vehicles
1118848789700 have 11 vehicles
1118848789800 have 11 vehicles
1118848789900 have 11 vehicles
1118848790000 have 11 vehicles
1118848790100 have 11 vehicles
1118848790200 have 11 vehicles
1118848790300 have 11 vehicles
1118848790400 have 11 vehicles
1118848790500 have 11 vehicles
1118848790600 have 11 vehicles
1118848790700 have 11 vehicles
1118848790800 have 11 vehicles
1118848790900 have 11 vehicles
1118848791000 have 11 vehicles
1118848791100 have 11 vehicles
1118848791200 have 11 vehicles
1118848791300 have 11 vehicles
1118848791400 have 11 vehicles
1118848791500 have 11 vehicles
1118848791600 have 11 vehicles
11188487

1118848819900 have 28 vehicles
1118848820000 have 28 vehicles
1118848820100 have 28 vehicles
1118848820200 have 28 vehicles
1118848820300 have 28 vehicles
1118848820400 have 28 vehicles
1118848820500 have 28 vehicles
1118848820600 have 28 vehicles
1118848820700 have 28 vehicles
1118848820800 have 28 vehicles
1118848820900 have 28 vehicles
1118848821000 have 28 vehicles
1118848821100 have 28 vehicles
1118848821200 have 28 vehicles
1118848821300 have 28 vehicles
1118848821400 have 28 vehicles
1118848821500 have 28 vehicles
1118848821600 have 28 vehicles
1118848821700 have 28 vehicles
1118848821800 have 28 vehicles
1118848821900 have 28 vehicles
1118848822000 have 28 vehicles
1118848822100 have 28 vehicles
1118848822200 have 28 vehicles
1118848822300 have 28 vehicles
1118848822400 have 28 vehicles
1118848822500 have 28 vehicles
1118848822600 have 28 vehicles
1118848822700 have 28 vehicles
1118848822800 have 29 vehicles
1118848822900 have 29 vehicles
1118848823000 have 29 vehicles
11188488

1118848809600 have 23 vehicles
1118848809700 have 23 vehicles
1118848809800 have 23 vehicles
1118848809900 have 23 vehicles
1118848810000 have 23 vehicles
1118848810100 have 23 vehicles
1118848810200 have 23 vehicles
1118848810300 have 23 vehicles
1118848810400 have 23 vehicles
1118848810500 have 23 vehicles
1118848810600 have 23 vehicles
1118848810700 have 23 vehicles
1118848810800 have 23 vehicles
1118848810900 have 24 vehicles
1118848811000 have 24 vehicles
1118848811100 have 24 vehicles
1118848811200 have 24 vehicles
1118848811300 have 24 vehicles
1118848811400 have 24 vehicles
1118848811500 have 24 vehicles
1118848811600 have 24 vehicles
1118848811700 have 24 vehicles
1118848811800 have 24 vehicles
1118848811900 have 24 vehicles
1118848812000 have 24 vehicles
1118848812100 have 25 vehicles
1118848812200 have 25 vehicles
1118848812300 have 25 vehicles
1118848812400 have 25 vehicles
1118848812500 have 25 vehicles
1118848812600 have 25 vehicles
1118848812700 have 25 vehicles
11188488

...

1118849426600 have 18 vehicles
1118849426700 have 18 vehicles
1118849426800 have 18 vehicles
1118849426900 have 18 vehicles
1118849427000 have 18 vehicles
1118849427100 have 18 vehicles
1118849427200 have 18 vehicles
1118849427300 have 18 vehicles
1118849427400 have 18 vehicles
1118849427500 have 18 vehicles
1118849427600 have 18 vehicles
1118849427700 have 18 vehicles
1118849427800 have 18 vehicles
1118849427900 have 18 vehicles
1118849428000 have 18 vehicles
1118849428100 have 18 vehicles
1118849428200 have 18 vehicles
1118849428300 have 18 vehicles
1118849428400 have 18 vehicles
1118849428500 have 18 vehicles
1118849428600 have 18 vehicles
1118849428700 have 18 vehicles
1118849428800 have 18 vehicles
1118849428900 have 18 vehicles
1118849429000 have 18 vehicles
1118849429100 have 18 vehicles
1118849429200 have 18 vehicles
1118849429300 have 18 vehicles
1118849429400 have 18 vehicles
1118849429500 have 18 vehicles
1118849429600 have 18 vehicles
1118849429700 have 18 vehicles
11188494

1118849458800 have 4 vehicles
1118849400900 have 32 vehicles
1118849401000 have 54 vehicles
1118849401100 have 54 vehicles
1118849401200 have 54 vehicles
1118849401300 have 54 vehicles
1118849401400 have 54 vehicles
1118849401500 have 54 vehicles
1118849401600 have 54 vehicles
1118849401700 have 54 vehicles
1118849401800 have 54 vehicles
1118849401900 have 54 vehicles
1118849357700 have 46 vehicles
1118849357800 have 46 vehicles
1118849357900 have 46 vehicles
1118849358000 have 47 vehicles
1118849358100 have 46 vehicles
1118849358200 have 46 vehicles
1118849358300 have 46 vehicles
1118849358400 have 46 vehicles
1118849358500 have 46 vehicles
1118849358600 have 46 vehicles
1118849358700 have 46 vehicles
1118849358800 have 46 vehicles
1118849358900 have 46 vehicles
1118849359000 have 46 vehicles
1118849359100 have 46 vehicles
1118849359200 have 46 vehicles
1118849359300 have 44 vehicles
1118849359400 have 44 vehicles
1118849359500 have 44 vehicles
1118849359600 have 45 vehicles
111884935

1118849386900 have 32 vehicles
1118849387000 have 33 vehicles
1118849387100 have 33 vehicles
1118849387200 have 32 vehicles
1118849387300 have 32 vehicles
1118849387400 have 32 vehicles
1118849387500 have 32 vehicles
1118849387600 have 32 vehicles
1118849387700 have 32 vehicles
1118849387800 have 32 vehicles
1118849387900 have 32 vehicles
1118849388000 have 32 vehicles
1118849388100 have 32 vehicles
1118849388200 have 32 vehicles
1118849388300 have 32 vehicles
1118849388400 have 32 vehicles
1118849388500 have 32 vehicles
1118849388600 have 32 vehicles
1118849388700 have 32 vehicles
1118849388800 have 32 vehicles
1118849388900 have 32 vehicles
1118849389000 have 31 vehicles
1118849389100 have 31 vehicles
1118849389200 have 31 vehicles
1118849389300 have 31 vehicles
1118849389400 have 31 vehicles
1118849389500 have 31 vehicles
1118849389600 have 32 vehicles
1118849389700 have 32 vehicles
1118849389800 have 32 vehicles
1118849389900 have 32 vehicles
1118849390000 have 32 vehicles
11188493

1118849418200 have 21 vehicles
1118849418300 have 21 vehicles
1118849418400 have 21 vehicles
1118849418500 have 21 vehicles
1118849418600 have 21 vehicles
1118849418700 have 21 vehicles
1118849418800 have 21 vehicles
1118849418900 have 21 vehicles
1118849419000 have 21 vehicles
1118849419100 have 21 vehicles
1118849419200 have 21 vehicles
1118849419300 have 21 vehicles
1118849419400 have 21 vehicles
1118849419500 have 21 vehicles
1118849419600 have 21 vehicles
1118849419700 have 21 vehicles
1118849419800 have 21 vehicles
1118849419900 have 21 vehicles
1118849420000 have 21 vehicles
1118849420100 have 21 vehicles
1118849420200 have 21 vehicles
1118849420300 have 21 vehicles
1118849420400 have 20 vehicles
1118849420500 have 20 vehicles
1118849420600 have 20 vehicles
1118849420700 have 20 vehicles
1118849420800 have 20 vehicles
1118849420900 have 20 vehicles
1118849421000 have 20 vehicles
1118849421100 have 20 vehicles
1118849421200 have 20 vehicles
1118849421300 have 20 vehicles
11188494

1118849450300 have 8 vehicles
1118849450400 have 8 vehicles
1118849450500 have 8 vehicles
1118849450600 have 8 vehicles
1118849450700 have 8 vehicles
1118849450800 have 8 vehicles
1118849450900 have 7 vehicles
1118849451000 have 7 vehicles
1118849451100 have 7 vehicles
1118849451200 have 7 vehicles
1118849451300 have 7 vehicles
1118849451400 have 7 vehicles
1118849451500 have 7 vehicles
1118849451600 have 7 vehicles
1118849451700 have 7 vehicles
1118849451800 have 7 vehicles
1118849451900 have 7 vehicles
1118849452000 have 7 vehicles
1118849452100 have 7 vehicles
1118849452200 have 7 vehicles
1118849452300 have 7 vehicles
1118849452400 have 7 vehicles
1118849452500 have 7 vehicles
1118849452600 have 7 vehicles
1118849452700 have 7 vehicles
1118849452800 have 7 vehicles
1118849452900 have 7 vehicles
1118849453000 have 7 vehicles
1118849453100 have 7 vehicles
1118849453200 have 7 vehicles
1118849453300 have 7 vehicles
1118849453400 have 7 vehicles
1118849453500 have 7 vehicles
1118849453